In [1]:
from ngsolve import *
import numpy as np
from ngsolve.meshes import Make1DMesh
from ngsolve.webgui import Draw
import scipy.sparse as sp
import scipy.sparse.linalg as spla
from scipy.sparse.linalg import eigs

In [2]:
L = 10.0
thick = 0.03
width = 0.01
E = 70e3
nu = 0
N0 = 1e-3

EI = E*width*thick**3/12
GS = E/2/(1+nu)*thick*width
kappa = 5.0/6.0

mapping = lambda x : (x*L)
mesh = Make1DMesh(100, mapping=mapping, periodic=False)

In [3]:
fes = H1(mesh, order=2, dirichlet="left|right")*H1(mesh, order=1, dirichlet="left") 
(w,beta),(dw,dbeta) = fes.TnT()

In [4]:
a = BilinearForm(fes, symmetric=False)
a += EI*(grad(beta)*grad(dbeta))*dx + kappa*GS*((grad(w)-beta)*(grad(dw)-dbeta))*dx

m = BilinearForm(fes,symmetric=False)
m += N0*grad(w)*grad(dw)*dx

a.Assemble()
m.Assemble()


In [5]:
freedofs = fes.FreeDofs()
print ("ndof =", fes.ndof)

ndof = 302


In [6]:
mat_a = sp.csr_matrix(a.mat.CSR())

In [7]:
mat_m = sp.csr_matrix(m.mat.CSR())

In [8]:
fd = list(freedofs)

In [9]:
fd_ = np.where(np.array(fd)==1)[0]
mat_1 = mat_a[:,fd_][fd_,:]
mat_2 = mat_m[:,fd_][fd_,:]

In [10]:
n_eig = 5
r_, w_ = eigs(A=mat_1, k=n_eig, M=mat_2, sigma=0.0)

In [11]:
print(r_.real)

[0.31805008 0.94033117 1.87415219 3.12032978 4.67984315]


numpy.ndarray